In [61]:
import whisper
from pytube import YouTube
import pickle
import pandas as pd
from tqdm import tqdm

In [8]:
model = whisper.load_model('medium')


100%|█████████████████████████████████████| 1.42G/1.42G [03:21<00:00, 7.57MiB/s]


In [66]:
videos = ['https://www.youtube.com/watch?v=8mQZzlQXK1Q', 
'https://www.youtube.com/watch?v=dJ1eDL15_Lw', 
'https://www.youtube.com/watch?v=ikYCr-0GAfw', 
'https://www.youtube.com/watch?v=2QO8tgSA6oQ',
'https://www.youtube.com/watch?v=-OM8RYUl_rg',
'https://www.youtube.com/watch?v=TGetyy-LKcY',
'https://www.youtube.com/watch?v=sDrakgSYvzc',
'https://www.youtube.com/watch?v=LmB3ZQ2F1MY',
'https://www.youtube.com/watch?v=CdyJ0iB_k00',
'https://www.youtube.com/watch?v=gGqbEH69ZaI',
'https://www.youtube.com/watch?v=2byXYrlDkZs',
'https://www.youtube.com/watch?v=QRQMPCs7m0E',
'https://www.youtube.com/watch?v=D1QKYLcvoU8',
'https://www.youtube.com/watch?v=5eyE20HpaCo',
'https://www.youtube.com/watch?v=XeeFp63L05k',
'https://www.youtube.com/watch?v=wKPPf9YNv5c',
'https://www.youtube.com/watch?v=xY2ftYAnUso',
'https://www.youtube.com/watch?v=gOt--6HPrIo',
'https://www.youtube.com/watch?v=L4zFpKpdub8',
'https://www.youtube.com/watch?v=4YhpWZCdiZc',
'https://www.youtube.com/watch?v=l2SNesXZoGM',
'https://www.youtube.com/watch?v=8-2WQF3SWwo',
'https://www.youtube.com/watch?v=bM0BeeA8RdY',
'https://www.youtube.com/watch?v=Zl7MbbgE4aU',
'https://www.youtube.com/watch?v=jQgkVKGqBCE',
'https://www.youtube.com/watch?v=8aDFvvjC6XM',
'https://www.youtube.com/watch?v=W3hMmZQAdhw']

#select the v= part of the url
vids = [x.split('=')[1] for x in videos]

In [82]:
for video in tqdm(videos[-2:]):
    yt = YouTube(video)
    #print video length
    print(yt.length, yt.title)
    yt.streams.filter(only_audio=True).first().download(filename = yt.title + '.mp4')
    print('downloaded', yt.title)
    #transcribe
    transcript = model.transcribe(yt.title + '.mp4')
    transcripts.append(transcript)

  0%|          | 0/2 [00:00<?, ?it/s]

1448 CBT Role-Play - Depressive Symptoms and Lack of Motivation
downloaded CBT Role-Play - Depressive Symptoms and Lack of Motivation


/Users/lsacy/opt/miniconda3/envs/chatbot/lib/python3.8/site-packages/whisper/transcribe.py:79: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")
 50%|█████     | 1/2 [14:57<14:57, 897.95s/it]

563 CBT for Social Anxiety Disorder: Using downward arrow and thought challenging techniques
downloaded CBT for Social Anxiety Disorder: Using downward arrow and thought challenging techniques


/Users/lsacy/opt/miniconda3/envs/chatbot/lib/python3.8/site-packages/whisper/transcribe.py:79: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")
100%|██████████| 2/2 [31:57<00:00, 958.69s/it]


In [141]:
# save transcripts to pickle
with open('data/whisper_transcripts.pkl', 'wb') as f:
    pickle.dump(transcripts, f)


In [142]:
# load pickle file 
with open('data/whisper_transcripts.pkl', 'rb') as f:
    transcripts = pickle.load(f)

transcripts

[{'text': " In this scenario, the client is angry at her work supervisor for making changes to her job. The counsellor listens as she tells the story of what happened when she got home. So Jane, it sounds like you're angry with your supervisor. Would I be right in saying that? Well I think I'm pretty angry. Many people with intellectual disabilities experience difficulty with abstract concepts. The use of emotion cards assist in clarifying the client's understanding of their emotions. Role play also helps the client to act out what happened and show the links between behaviours and their consequences. It allows the client to act out the story as they remember. Alright, well look, maybe to help me understand more about that anger, I'm wondering if you could choose two or three pictures here that look like how you were angry at the time. Which of the cards here would show how angry you were? Alright, okay, I might just have a look at those. Okay. It does look like anger, doesn't it? It's

In [202]:
# create a dataframe with columns: video_id, utterance, type, dialogue_act
df2 = pd.DataFrame(columns = ['video_id', 'utterance', 'type', 'dialogue_act'])

In [207]:
for j in range(len(transcripts)):
    video_id = j
    for i in range(len(transcripts[j]['segments'])):
        utterance = transcripts[j]['segments'][i]['text']
        df2.loc[len(df2)] = [video_id, utterance, 'NaN', 'NaN']

In [216]:
# set the column type and dialogue_act to empty
df2['type'] = ''
df2['dialogue_act'] = ''

In [219]:
# save the dataframe to a csv file
df2.to_csv('data/whisper_transcripts_utterances.csv', index = False)

In [226]:
df_full_converstation = pd.DataFrame(columns = ['video_id', 'conversation']) 
for i in range(len(transcripts)):
    video_id = i
    conversation = transcripts[i]['text']
    df_full_converstation.loc[len(df_full_converstation)] = [video_id, conversation]


In [235]:
df_full_converstation.to_csv('data/whisper_transcripts_full_conversation.csv', index = False)